In [12]:
import pandas as pd
import numpy as np
from time import time
import json
from sqlalchemy import create_engine
import re
import datetime
from mpl_toolkits.basemap import Basemap

%matplotlib inline
import matplotlib.pyplot as plt
import seaborn as sns; sns.set()
plt.style.use('seaborn-whitegrid')
import numpy as np
from mpl_toolkits.basemap import Basemap
from geopy.distance import distance as dist

import plotly
import chart_studio.plotly as py
import plotly.graph_objs as go
plotly.offline.init_notebook_mode()

In [2]:
# Set up the SQL connection
dbname = 'redshift'
url = 'panamera-ods.cnsuxis6zqxr.us-west-2.redshift.amazonaws.com:5439/panameraods'
engine = create_engine("postgresql://" + 'lucasdresl' + ":" + 'cQsY801a76x82x62aWDT' + "@" + url)


## Lat and Long de los ads

In [5]:
query = """

drop table if exists listings_activos;
select
    id,
    category_id
into temp table listings_activos
  from livesync.panamera_ads
 where status='active'
   and livesync_dbname='olxin'
group by 1,2;

select
    ad_id,map_lat,map_lon,category_id
   from livesync.panamera_locations a
     join listings_activos b on a.ad_id=b.id
  where livesync_dbname='olxin'
group by 1,2,3,4

"""

In [6]:
df = pd.read_sql_query(query.replace('%', '%%'), engine)


In [26]:
df.head()

ad_id   map_lat   map_lon  category_id
0  729373253  16.97656  81.79025         1795
1  744509711  30.37304  76.14047         1725
2  750454192  17.26173  80.16230         1729
3  803164571  28.63531  77.07409          625
4  836308897  18.93705  72.82829           84

In [32]:
df.shape

(3214568, 4)

In [28]:
coords = pd.concat([df['map_lat'], df['map_lon']], axis=1)
coords = coords.sample(frac=0.02, replace=True, random_state=42)
print("sample size: {}".format(coords.shape[0]))

sample size: 64291


In [31]:
fig = go.Figure(data=go.Scattergeo(
        lon = coords['map_lon'],
        lat = coords['map_lat'],
        mode = 'markers',
      
        ))

fig.update_layout(
        title = 'Active listings',
        geo_scope='asia',
    )
fig.show()